In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
import pandas as pd

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)

spark = SparkSession.builder.getOrCreate()

# Load Data

In [0]:
profiles = spark.read.parquet('/linkedin/people')
print(profiles.count())
# profiles.display()

3462290


In [0]:
companies = spark.read.parquet('/linkedin/companies')
print(companies.count())

1422797


# Filtering the Data  and getting the relevant records

In [0]:
from pyspark.sql.functions import explode, col, size, lower

x = profiles.filter(size(col('posts')) != 0)
nx=x.select(explode("posts").alias("exploded_posts"))
nx = nx.withColumn("title_lower", lower(col('exploded_posts.title')))

relevant_words = ['work from home', 'parttime', 'work with us', 'job', 'position', 'open position', 'hiring', 'hire', 'join our team', 'recruiting', 'role', 'career opportunity', 'full-time', 'full time', 'part time', 'part-time', 'entry level', 'fulltime','apply now']

# Construct a filter condition
condition = col('title_lower').contains(relevant_words[0])
for word in relevant_words[1:]:
    condition = condition | col('title_lower').contains(word)

# Filter the DataFrame based on the condition
nx = nx.filter(condition)
nx1=nx.select(col('exploded_posts')['title'], col('exploded_posts')['link'])
print(nx1.count())

3344


In [0]:
nx1.display()

exploded_posts.title exploded_posts.link 10 Reasons to Hire Vets https://www.linkedin.com/pulse/10-reasons-hire-vets-tom-hildreth?trk=public_profile_article_view Facing a Change - Job Search 1st Month https://www.linkedin.com/pulse/facing-change-job-search-1st-month-ilya-kotlyar?trk=public_profile_article_view The Role Of Observability In Improving Reliability https://www.linkedin.com/pulse/role-observability-improving-systems-reliability-rodrigo-f-santos?trk=public_profile_article_view Home Care job available https://www.linkedin.com/pulse/home-care-job-available-lizbeth-zielinski?trk=public_profile_article_view Hiring https://www.linkedin.com/pulse/hiring-heather-goodell?trk=public_profile_article_view Psychology’s Role in Marketing https://www.linkedin.com/pulse/psychologys-role-marketing-hadley-roy?trk=public_profile_article_view Customer Service 5 to 10 positions available https://www.linkedin.com/pulse/customer-service-5-10-positions-available-stephanie-litchfield?trk=public_profile_article_view Clarifying Roles to Optimize Safe Outcomes during Confined Space Operations https://www.linkedin.com/pulse/clarifying-roles-optimize-safe-outcomes-during-confined-emma-mcclees?trk=public_profile_article_view Better healthcare can ease the small business hiring crisis. Congress must help. https://www.linkedin.com/pulse/better-healthcare-can-ease-small-business-hiring-must-liz-wilke-phd?trk=public_profile_article_view I need a job in the Cleveland, Ohio area https://www.linkedin.com/pulse/20140326013126-3818119-i-need-a-job-in-the-cleveland-ohio-area?trk=public_profile_article_view JOB ALERT https://www.linkedin.com/pulse/job-alert-susan-portugal?trk=public_profile_article_view GREAT CSR JOB IN LONDON! https://www.linkedin.com/pulse/great-csr-job-london-susan-portugal?trk=public_profile_article_view Wonderful Job Opportunity At Points of Light https://www.linkedin.com/pulse/wonderful-job-opportunity-points-light-susan-portugal?trk=public_profile_article_view We are hiring... https://www.linkedin.com/pulse/we-hiring-tiffany-taylor?trk=public_profile_article_view Job Posting: Omadi - Senior Implementation Engineer https://www.linkedin.com/pulse/job-posting-omadi-senior-implementation-engineer-daniel-marsh?trk=public_profile_article_view Recruiting: Want to hire a gritty, scrappy performer? Why you should hire a swimmer. Or any other proven, disciplined athlete. https://www.linkedin.com/pulse/recruiting-want-hire-gritty-scrappy-performer-why-you-dan-larson?trk=public_profile_article_view Marcotte is hiring a Group Benefits Department Manager. https://www.linkedin.com/pulse/marcotte-hiring-group-benefits-department-manager-trish-maynard?trk=public_profile_article_view Marcotte is hiring Group Benefits Department Manager position. https://www.linkedin.com/pulse/marcotte-hiring-group-benefits-department-manager-position-maynard?trk=public_profile_article_view JSOM: Mastering Job Interviews https://www.linkedin.com/pulse/jsom-mastering-job-interviews-faiz-prasla?trk=public_profile_article_view Executive Director Position https://www.linkedin.com/pulse/executive-director-position-jennifer-williams?trk=public_profile_article_view I Should Never Have Hired You. You Have too Many Children. https://www.linkedin.com/pulse/i-should-never-have-hired-you-too-many-children-angela-christu?trk=public_profile_article_view Full Time Java Architects/Java Developers Required!!! https://www.linkedin.com/pulse/full-time-java-architectsjava-developers-required-chris-jones?trk=public_profile_article_view Industrial Post-Doctoral position - Molecular Virology https://www.linkedin.com/pulse/industrial-post-doctoral-position-molecular-jason-laliberte?trk=public_profile_article_view Career Opportunity https://www.linkedin.com/pulse/career-opportunity-bibiana-torres?trk=public_profile_article_view Construction site safety jobs available https://www.linkedin.com/pulse/construction-site-safety-jobs-available-dan-bergerson-chst?trk=public_profile_article_view Growin

# Web Scraping for the posts

In [0]:
! pip install bs4

     |████████████████████████████████| 147 kB 26.2 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-ddc19c6c-6c93-4807-9e25-40ae1fb471a7/bin/python -m pip install --upgrade pip' command.


In [0]:
from bs4 import BeautifulSoup
import requests
import json

proxy_username = 'brd-customer-hl_80709a30-zone-kinan_samar_rawan_proxy'
proxy_password = 'aezku7l5zcug'
proxy_host = 'brd.superproxy.io:9515'

proxy_url = {'http': f"http://{proxy_username}:{proxy_password}@{proxy_host}"}

urls = nx.select('exploded_posts.link').collect()
titles = [sen[0] for sen in nx.select('exploded_posts.title').collect()]

print(len(titles))
posts = []
pops_list = []
for j in range(len(urls)):
    # print(j)
    response = requests.get(urls[j][0], proxies=proxy_url)
    res_body = response.text

    soup = BeautifulSoup(res_body, "html.parser")
    try:
        books_containers = soup.find('div', class_ = 'article-main__content max-w-[744px]')
        para = books_containers.find_all('p')
        temp = ""
        for i in range(len(para)):
            temp += (para[i].text) + " "
        posts.append(temp)
    except:
        pops_list.append(j)

3344


In [0]:
links = [sen[0] for sen in nx.select('exploded_posts.link').collect()]
# print(len(links))
l = pops_list.copy()
l.sort(reverse=True)
for index in l:
    if index < len(links):
        del links[index]
print(len(links))

3310


In [0]:
l = pops_list.copy()
x = titles.copy()
l.sort(reverse=True)
for index in l:
    if index < len(x):
        del x[index]
print(len(x))

3310


# Create DataFrame and downloading it 

In [0]:
data = list(zip(x, posts, links))

In [0]:
df_answers = spark.createDataFrame(data, schema=['Title', 'post_content', 'post_link'])

In [0]:
df_answers.display()

Title post_content post_link 10 Reasons to Hire Vets Looking for a hard-working, motivated, ethical employee? Try hiring a U.S. veteran. Veterans are disciplined team players that can bolster any employer's business. What's more, hiring veterans is not only a good idea, it's good business. Here are 10 more reasons to hire veterans: 1.   Accelerated learning curve: Veterans have the proven ability to learn new skills and concepts. In addition, they can enter your workforce with identifiable and transferable skills, proven in real-world situations. This background can enhance your organization's productivity. 2.   Leadership: The military trains people to lead by example as well as through direction, delegation, motivation, and inspiration. Veterans understand the practical ways to manage behaviors for results, even in the most trying circumstances. They also know the dynamics of leadership as part of both hierarchical and peer structures. 3.   Teamwork. Veterans understand how genuine teamwork grows out of a responsibility to one's colleagues. Military duties involve a blend of individual and group productivity. They also necessitate a perception of how groups of all sizes relate to each other and an overarching objective. 4.   Diversity and inclusion in action: Veterans have learned to work side by side with individuals regardless of diverse race, gender, geographic origin, ethnic background, religion, and economic status as well as mental, physical, and attitudinal capabilities. They have the sensitivity to cooperate with many different types of individuals. 5.   Efficient performance under pressure: Veterans understand the rigors of tight schedules and limited resources. They have developed the capacity to know how to accomplish priorities on time, in spite of tremendous stress. They know the critical importance of staying with a task until it is done right. 6.   Respect for procedures: Veterans have gained a unique perspective on the value of accountability. They can grasp their place within an organizational framework, becoming responsible for subordinates' actions to higher supervisory levels. They know how policies and procedures enable an organization to exist. 7.   Technology and globalization: Because of their experiences in the service, veterans are usually aware of international and technical trends pertinent to business and industry. They can bring the kind of global outlook and technological savvy that all enterprises of any size need to succeed. 8.   Integrity: Veterans know what it means to do "an honest day's work." Prospective employers can take advantage of a track record of integrity, often including security clearances. This integrity translates into qualities of sincerity and trustworthiness. 9.   Conscious of health and safety standards: Thanks to extensive training, veterans are aware of health and safety protocols both for themselves and the welfare of others. Individually, they represent a drug-free workforce that is cognizant of maintaining personal health and fitness. On a company level, their awareness and conscientiousness translate into protection of employees, property, and materials. 10.                 Triumph over adversity: In addition to dealing positively with the typical issues of personal maturity, veterans have frequently triumphed over great adversity. They likely have proven their mettle in mission critical situations demanding endurance, stamina, and flexibility. They may have overcome personal disabilities through strength and determination. Employers looking for veterans can visit the Employer Resource Center. https://www.linkedin.com/pulse/10-reasons-hire-vets-tom-hildreth?trk=public_profile_article_view Facing a Change - Job Search 1st Month (23 to be more precise) since I found myself in this position – being fresh on the market, molding the next chapter of my career. My only other time thus far was when I was getting out of university in 2000.  If you recall that year and the fo